In [1]:
import numpy as np
from numpy import linalg as LA
import pandas as pd
import math
import scipy.optimize as optimize
import spiceypy

In [2]:
pip install poliastro

  Using cached poliastro-0.17.0-py3-none-any.whl.metadata (11 kB)
  Using cached astroquery-0.4.7-py3-none-any.whl.metadata (7.2 kB)
  Using cached keyring-25.2.0-py3-none-any.whl.metadata (20 kB)
  Using cached pyvo-1.5.1-py3-none-any.whl.metadata (4.7 kB)
Using cached poliastro-0.17.0-py3-none-any.whl (162 kB)
Using cached astroquery-0.4.7-py3-none-any.whl (5.3 MB)
Using cached keyring-25.2.0-py3-none-any.whl (38 kB)
Using cached pyvo-1.5.1-py3-none-any.whl (910 kB)
Note: you may need to restart the kernel to use updated packages.


In [3]:
from astropy import units as u
from astropy import constants as const
from astropy.time import Time
from astropy.coordinates import get_body_barycentric_posvel
from poliastro.bodies import Sun, Earth
from poliastro.twobody import Orbit

In [19]:
folder='/home/unipi/v.vichi3/Desktop/'
df=pd.read_csv(folder+'neos_dataframe.csv')

In [20]:
df.head()

Unnamed: 0     spkid pha      H  epoch_mjd       e      a      i      om  \
0           0  20000433   N  10.41      60400  0.2227  1.458  10.83  304.28   
1           1  20000719   N  15.59      60400  0.5469  2.636  11.58  183.85   
2           2  20000887   N  13.88      60400  0.5710  2.472   9.40  110.42   
3           3  20001036   N   9.26      60400  0.5328  2.665  26.69  215.50   
4           4  20001221   N  17.38      60400  0.4352  1.920  11.88  171.31   

        w      ma    moid  
0  178.90  334.73  0.1500  
1  156.22  102.37  0.2010  
2  350.48  289.48  0.0803  
3  132.48  321.69  0.3450  
4   26.68  197.64  0.1080

In [21]:
#Mean anomaly to true anomaly
def kepler_equation(M,E,e):
    #M=mean anomaly, E=#eccentric anomaly, e=eccentricity
    return E-e*np.sin(E)-M
def mean_to_true_an(M,e):
    E=optimize.newton(kepler_equation, M, args=(M,e))
    nu=math.atan2(math.sin(E)*math.sqrt(1-e**2),math.cos(E)-e) #true anomaly in radians
    return math.degrees(nu)

In [22]:
#Perform the conversion for each element of the DataFrame
N=df.shape[0]
nu=np.zeros((N,))
for el in range(N):
    nu[el]=mean_to_true_an(df['ma'][el],df['e'][el])
df['nu']=nu

In [23]:
#Keplerian to Cartesian elements
def kep_to_car(a,e,i,om,w,nu):
    orb=Orbit.from_classical(Sun, a<<u.AU, e<<u.one, i<<u.deg, om<<u.deg, w<<u.deg, nu<<u.deg)
    r=orb.r.to(u.AU)
    v=orb.v.to(u.AU/u.d)
    return r,v

In [24]:
#Perform the conversion for each element of the DataFrame
car=np.zeros((N,6))
for el in range(N):
    car[el,:3],car[el,3:]=kep_to_car(df['a'][el],df['e'][el],df['i'][el],df['om'][el],df['w'][el],df['nu'][el])
    if (el%10000==0):
        print(f"{el} completed")
car_df=pd.DataFrame(car, columns=['x','y','z','vx','vy','vz'])
car_df['EPOCH']=df['epoch_mjd']

0 completed
10000 completed
20000 completed
30000 completed


In [26]:
car_df.head()

x         y         z        vx        vy        vz  EPOCH
0 -1.043768 -0.948369 -0.267177  0.007095 -0.012608 -0.000237  60400
1  0.009877  2.220705 -0.453875 -0.010286  0.006398 -0.001450  60400
2 -0.590315  0.914974  0.038736 -0.018393 -0.008600  0.003350  60400
3  0.888349  1.323366 -0.282285 -0.008231  0.011640 -0.007167  60400
4  2.682621  0.150702 -0.116604  0.000993  0.007884 -0.001671  60400

In [27]:
#Cartesian to Attributable elements
def car_to_att(r_sun, v_sun, epoch):
    #r_sun, v_sun are the Cartesian heliocentric elements of the asteroid
    #epoch is in MJD
    earth_posvel=get_body_barycentric_posvel('earth',Time(epoch,format='mjd'))
    r_earth=earth_posvel[0].xyz
    v_earth=earth_posvel[1].xyz

    #Cartesian geocentric elements
    r=r_sun-r_earth
    v=v_sun-v_earth

    #Rotation to the equatorial reference frame
    roteceq=spiceypy.spiceypy.pxform("ECLIPJ2000","J2000",0)
    r=roteceq.dot(r)
    v=roteceq.dot(v)

    rho=LA.norm(r)
    dz=r[0]**2+r[1]**2
    epsilon=np.finfo(float).eps
    if (dz.value<100*epsilon):
        ra=0
    else: ra=np.arctan2(r[1],r[0]) #in radians
    dec=np.arcsin(r[2]/rho)

    #Computation of first derivatives
    dadx=np.zeros((3,1))<<u.one/u.AU
    dddx=np.zeros((3,1))<<u.one/u.AU
    dadx[0]=-r[1]/dz
    dadx[1]=r[0]/dz
    dadx=dadx.reshape(1,-1) #transform dadx into a row vector
    dddx[0]=-r[2]*(r[0]/(np.sqrt(dz)*rho**2))
    dddx[1]=-r[2]*(r[1]/(np.sqrt(dz)*rho**2))
    dddx[2]=np.sqrt(dz)/rho**2
    dddx=dddx.reshape(1,-1)

    rho_dot=np.dot(r,v)/rho
    ra_dot=np.dot(dadx,v) #in 1/day
    dec_dot=np.dot(dddx,v) #in 1/day
    cos_ra=np.cos(ra)
    sin_ra=np.sin(ra)
    sin_dec=np.sin(dec)
    return [cos_ra.value,sin_ra.value,sin_dec.value, ra_dot[0].value, dec_dot[0].value]

In [28]:
#Perform the conversion for each element of the DataFrame
attr=np.zeros((N,5))
for el in range(N):
    attr[el,:]=car_to_att(car_df.iloc[el,0:3]<<u.AU, car_df.iloc[el,3:6]<<u.AU/u.d, car_df['EPOCH'][el])
    if (el%10000==0):
        print(f"{el} completed")

0 completed
10000 completed
20000 completed
30000 completed


In [29]:
attr_df=pd.DataFrame(attr,columns=['cos_ra','sin_ra','sin_dec','ra_dot','dec_dot'])

In [30]:
attr_df['MOID']=df['moid']
attr_df.head()

cos_ra    sin_ra   sin_dec    ra_dot   dec_dot    MOID
0 -0.084129 -0.996455 -0.606347  0.006616  0.006707  0.1500
1  0.392310  0.919833  0.229663  0.007516  0.004055  0.2010
2  0.387645  0.921809  0.459919  0.019881  0.011605  0.0803
3  0.791026  0.611783  0.166871  0.011227  0.003821  0.3450
4  0.996437  0.084345  0.023712  0.005317  0.003798  0.1080

In [31]:
attr_df.to_csv(folder+'neos_attr.csv',index=False)